In [1]:
import os
os.environ['DJANGO_SETTINGS_MODULE'] = 'cashup_backend.settings'
os.environ['DJANGO_ALLOW_ASYNC_UNSAFE'] = "true"

import django
django.setup()

In [3]:
from data.models import MinuteData, HourData, UpFlow, DownFlow

In [4]:
import requests
from datetime import timedelta, datetime

In [5]:
up_dn_list = []
last_data = []
dn_list = []
up_list = []
new_dn_list = []
new_up_list = []
other_up_dn_list = []

continue_up_down = "D0"
prev_up_down = "S"
work_1_0_1 = "S"
work_1_5_1 = "S"
work_1_0_2 = "S"
work_1_5_2 = "S"
last_time_1_0_1 = datetime.now()
last_time_1_5_1 = datetime.now()
last_time_1_0_2 = datetime.now()
last_time_1_5_2 = datetime.now()

last_dn, last_up = "", ""

max_price, min_price = 0, 0
work_up_high, work_dn_low = 1000000, 0
volume = 0
prev_low = 0
prev_high = 100000
start = 0
last_up = 0
last_dn = 0
volume_up_dn = ""
hour_up_down = ""
prev_signal_down_price = 0
prev_signal_up_price = 0

base_price = 0
flow_base_price = 0
prev_signal = ""
flow_list = []
flow_element_list = []
prev_down_flow = 0
prev_up_flow = 0
down_flow = ['DN', 'DN', 'UP', 'UP']
up_flow = ['UP', 'UP', 'DN', 'DN']
down_flow_list = []
up_flow_list = []
last_down_flow_time = ""
last_up_flow_time = ""
down_flow_element_list = []
down_flow_confirm_list = []
up_flow_element_list = []
up_flow_confirm_list = []

In [6]:
while True:
    URL = "https://www.bitmex.com/api/v1/trade/bucketed?symbol=XBT&binSize=5m&partial=false&start={}&count=1000&reverse=false".format(start)
    req = requests.get(URL).json()
    for data in req:
        volume_up_dn = ""
        signal = ""
        signal_price = 0
        hour_up_down = ""
        now_work_1_0_1 = ""
        now_work_1_5_1 = ""
        now_work_1_0_2 = ""
        now_work_1_5_2 = ""
        datetime = datetime.strptime(data['timestamp'].replace("T", " ")[0:19], "%Y-%m-%d %H:%M:%S") + timedelta(hours=9) - timedelta(minutes=5)
        open_price = data['open'] if data['open'] != None else 0
        high_price = data['high'] if data['high'] != None else 0
        low_price = data['low'] if data['low'] != None else 0
        close_price = data['close'] if data['close'] != None else 0
        avg_price = (high_price + low_price) / 2
        
        if volume != 0:
            volume_rate = data['volume'] / volume
        else:
            volume_rate = 0
            
        volume = data['volume']

        flag = False

        if open_price > close_price:
            UD = "D"

        elif open_price < close_price:
            UD = "U"

        else:
            UD = "S"

        if len(last_data) > 3:
            last_data.pop(0)
            volume_bigger_count = 0
            volume_smaller_count = 0

            for i in last_data:
                if i[2] < volume:
                    volume_bigger_count += 1

                if i[2] > volume:
                    volume_smaller_count += 1

            if volume_bigger_count == 3:
                volume_up_dn = "UP"

            if volume_smaller_count == 3:
                volume_up_dn = "DN"

        last_data.append([low_price, high_price, volume])
        
        if continue_up_down[0] == "U":
            if UD == "U":
                continue_up_down = "U" + str(int(continue_up_down[1:]) + 1)
            elif UD == "D":
                continue_up_down = "D1"
        else:
            if UD == "U":
                continue_up_down = "U1"
            elif UD == "D":
                continue_up_down = "D" + str(int(continue_up_down[1:]) + 1)
        
        if len(up_dn_list) > 3:
            up_dn_list.pop(0)
        up_dn_list.append(UD)
        
        if up_dn_list.count("U") > 2:
            if high_price >= last_up:
                hour_up_down = "UP(U)"
            else:
                hour_up_down = "UP(D)"
            last_up = high_price
        
        if up_dn_list.count("D") > 2:
            if low_price >= last_dn:
                hour_up_down = "DN(U)"
            else:
                hour_up_down = "DN(D)"
            last_dn = low_price
        
        if UD == "U":
            if other_up_dn_list.count("D") > 2:
                other_up_dn_list.reverse()
                up_list.reverse()
                dn_list.reverse()
                count = 0
                max_price_list = []
                min_price_list = []
                is_U = False
                for idx, element in enumerate(other_up_dn_list):
                    if element == "D":
                        count += 1
                        max_price_list.append(dn_list[idx])
                    else:
                        is_U = True
                    if is_U and count >= 3:
                        if element == "U":
                            break
                        else:
                            min_price_list.append(up_list[idx])
                            break
                    min_price_list.append(up_list[idx])

                if prev_up_down == "D" and max(max_price_list) == max_price_list[len(max_price_list) - 1]:
                    if prev_signal_down_price != 0:
                        if prev_signal_down_price < min(min_price_list):
                            signal = "fD(U)"
                        elif prev_signal_down_price == min(min_price_list):
                            signal = "fD(0)"
                        else:
                            signal = "fD(D)"
                    prev_signal_down_price = min(min_price_list)
                other_up_dn_list.reverse()
                up_list.reverse()
                dn_list.reverse()

        if UD == "D":
            if other_up_dn_list.count("U") > 2:
                other_up_dn_list.reverse()
                up_list.reverse()
                dn_list.reverse()
                count = 0
                max_price_list = []
                min_price_list = []
                is_D = False
                for idx, element in enumerate(other_up_dn_list):
                    if element == "U":
                        count += 1
                        min_price_list.append(up_list[idx])
                    else:
                        is_D = True

                    if is_D and count >= 3:
                        if element == "D":
                            break
                        else:
                            max_price_list.append(dn_list[idx])
                            break
                    max_price_list.append(dn_list[idx])

                if prev_up_down == "U" and min(min_price_list) == min_price_list[len(min_price_list) - 1]:
                    print(datetime)
                    print(other_up_dn_list)
                    print(max_price_list, min_price_list)
                    if prev_signal_down_price != 0:
                        if prev_signal_up_price < max(max_price_list):
                            signal = "fU(U)"
                        elif prev_signal_up_price == max(max_price_list):
                            signal = "fU(0)"
                        else:
                            signal = "fU(D)"
                    prev_signal_up_price = max(max_price_list)
                other_up_dn_list.reverse()
                up_list.reverse()
                dn_list.reverse()
                    
        if len(dn_list) > 5:
            dn_list.pop(0)
        dn_list.append(high_price)
            
        if len(up_list) > 5:
            up_list.pop(0)
        up_list.append(low_price)
        
        if len(other_up_dn_list) > 5:
            other_up_dn_list.pop(0)
        other_up_dn_list.append(UD)
        
        if volume_up_dn == "UP":
            if (max_price < high_price) and (volume_rate > 1):
                if work_1_0_1[0] == "U":
                    if datetime == last_time_1_0_1 + timedelta(hours=1):
                        continue_flag_1_0_1 = True
                    else:
                        work_1_0_1 = "U" + str(int(work_1_0_1[1:]) + 1)
                else:
                    work_1_0_1 = "U1"
                
                now_work_1_0_1 = work_1_0_1
                last_time_1_0_1 = datetime
            
            if (min_price > low_price) and (volume_rate > 1):
                if work_1_0_1[0] == "D":
                    if datetime == last_time_1_0_1 + timedelta(hours=1):
                        continue_flag_1_0 = True
                    else:
                        work_1_0_1 = "D" + str(int(work_1_0_1[1:]) + 1)
                
                else:
                    work_1_0_1 = "D1"
                
                now_work_1_0_1 = work_1_0_1
                last_time_1_0_1 = datetime
                
            if (max_price < high_price) and (volume_rate > 1.5):
                if work_1_5_1[0] == "U":
                    if datetime == last_time_1_5_1 + timedelta(hours=1):
                        continue_flag_1_5_1 = True
                    else:
                        work_1_5_1 = "U" + str(int(work_1_5_1[1:]) + 1)
                else:
                    work_1_5_1 = "U1"
                
                now_work_1_5_1 = work_1_5_1
                last_time_1_5_1 = datetime
            
            if (min_price > low_price) and (volume_rate > 1.5):
                if work_1_5_1[0] == "D":
                    if datetime == last_time_1_5_1 + timedelta(hours=1):
                        pass
                    else:
                        work_1_5_1 = "D" + str(int(work_1_5_1[1:]) + 1)
                
                else:
                    work_1_5_1 = "D1"
                
                now_work_1_5_1 = work_1_5_1
                last_time_1_5_1 = datetime

            if (max_price < high_price and min_price < low_price) and (volume_rate > 1):
                if work_1_0_2[0] == "U":
                    if datetime == last_time_1_0_2 + timedelta(hours=1):
                        pass
                    else:
                        work_1_0_2 = "U" + str(int(work_1_0_2[1:]) + 1)
                else:
                    work_1_0_2 = "U1"
                
                now_work_1_0_2 = work_1_0_2
                last_time_1_0_2 = datetime
            
            if (min_price > low_price and max_price > high_price) and (volume_rate > 1):
                if work_1_0_2[0] == "D":
                    if datetime == last_time_1_0_2 + timedelta(hours=1):
                        pass
                    else:
                        work_1_0_2 = "D" + str(int(work_1_0_2[1:]) + 1)
                
                else:
                    work_1_0_2 = "D1"
                
                now_work_1_0_2 = work_1_0_2
                last_time_1_0_2 = datetime     
                
                
            if (max_price < high_price and min_price < low_price) and (volume_rate > 1.5):
                if work_1_5_2[0] == "U":
                    if datetime == last_time_1_5_2 + timedelta(hours=1):
                        pass
                    else:
                        work_1_5_2 = "U" + str(int(work_1_5_2[1:]) + 1)
                else:
                    work_1_5_2 = "U1"
                
                now_work_1_5_2 = work_1_5_2
                last_time_1_5_2 = datetime
            
            if (min_price > low_price and max_price > high_price) and (volume_rate > 1.5):
                if work_1_5_2[0] == "D":
                    if datetime == last_time_1_5_1 + timedelta(hours=1):
                        pass
                    else:
                        work_1_5_2 = "D" + str(int(work_1_5_2[1:]) + 1)
                
                else:
                    work_1_5_2 = "D1"
                
                now_work_1_5_2 = work_1_5_2
                last_time_1_5_2 = datetime

            max_price, min_price = high_price, low_price
            
        if now_work_1_0_1 != "":
            now_work_1_0_1 = "w" + now_work_1_0_1
        
        if now_work_1_5_1 != "":
            now_work_1_5_1 = "w" + now_work_1_5_1
            
        if now_work_1_0_2 != "":
            now_work_1_0_2 = "w" + now_work_1_0_2
            
        if now_work_1_5_2 != "":
            now_work_1_5_2 = "w" + now_work_1_5_2
        
        flow = ""
        if flow_base_price != 0:
            if prev_signal == "fU(D)":
                if low_price > flow_base_price:
                    flow = "UP"
                else:
                    flow = "DN"
            if prev_signal == "fD(U)":
                if high_price > flow_base_price:
                    flow = "UP"
                else:
                    flow = "DN"

        if signal == "fU(D)":
            flow_base_price = high_price
            prev_signal = signal

        if signal == "fD(U)":
            flow_base_price = low_price
            prev_signal = signal

        if flow != "":
            if len(flow_list) > 3:
                flow_list.pop(0)
                flow_element_list.pop(0)
            flow_list.append(flow)
            flow_element_list.append({
                'datetime': datetime,
                'min_price': low_price,
                'max_price': high_price
            })
            
        flow_element = None

        if flow_list == down_flow:
            if prev_down_flow != 0:
                flow_element = DownFlow()
                flow_element.datetime = flow_element_list[1]['datetime']
                flow_element.base_price = flow_element_list[1]['max_price']
                if prev_down_flow < flow_element_list[1]['max_price']:
                    flow_element.down_flow = "UP"
                else:
                    flow_element.down_flow = "DN"
                if len(down_flow_list) > 4:
                    down_flow_list.pop(0)
                down_flow_list.append(flow_element.down_flow)

                if len(down_flow_list) > 4:
                    if down_flow_list.count("UP") > 3:
                        flow_element.down_flow_confirm = "UP"

                    if down_flow_list.count("DN") > 3:
                        flow_element.down_flow_confirm = "DN"
                        
                    if down_flow_list.count("UP") == 5:
                        flow_element.down_flow_trade = "B#4"                      

            prev_down_flow = flow_element_list[1]['max_price']

        if flow_list == up_flow:
            if prev_up_flow != 0:
                flow_element = UpFlow()
                flow_element.datetime = flow_element_list[1]['datetime']
                flow_element.base_price = flow_element_list[1]['min_price']
                if prev_up_flow < flow_element_list[1]['min_price']:
                    flow_element.up_flow = "UP"
                else:
                    flow_element.up_flow = "DN"

                if len(up_flow_list) > 4:
                    up_flow_list.pop(0)
                up_flow_list.append(flow_element.up_flow)

                if len(up_flow_list) > 4:
                    if up_flow_list.count("UP") > 3:
                        flow_element.up_flow_confirm = "UP"

                    if up_flow_list.count("DN") > 3:
                        flow_element.up_flow_confirm = "DN"
                    
                    if up_flow_list.count("DN") == 5:
                        flow_element.up_flow_trade = "S#4"

            prev_up_flow = flow_element_list[1]['min_price']

        if len(flow_element_list) > 3:
            if flow_element:
                flag = False
                if type(flow_element) == UpFlow:
                    flag = True
                
                if not flag and flow_element.down_flow_confirm == "UP":
                    last_down_flow_time = flow_element_list[1]['datetime']

                if flag and flow_element.up_flow_confirm == "DN":
                    last_up_dlow_time = flow_element_list[1]['datetime']

                if not flag and flow_element.down_flow:
                    if last_down_flow_time != "":
                        if flow_element_list[1]['datetime'] - last_down_flow_time > timedelta(hours=2):
                            if HourData.objects.filter(datetime__range=[last_down_flow_time, flow_element_list[1]['datetime'] - timedelta(hours=1)], up_down='U').values('up_down').count() > 1:
                                flow_element.down_flow_trade = "S#1"
                                last_down_flow_time = ""

                    elif down_flow_list[-2:] == ['UP', 'UP']:
                        flow_element.down_flow_trade = "S#3"

                    if len(down_flow_element_list) > 1:
                        down_flow_element_list.pop(0)
                    down_flow_element_list.append(flow_element)
                    
                    
                    if len(down_flow_element_list) > 1:
                        if down_flow_element_list[0].down_flow_confirm is None and flow_element.down_flow_confirm == "DN":
                            flow_element.down_flow_trade = "B#2"

                if flag and flow_element.up_flow:
                    if last_up_flow_time != "":
                        if flow_element_list[1]['datetime'] - last_up_flow_time > timedelta(hours=2):
                            if HourData.objects.filter(datetime__range=[last_up_flow_time, flow_element_list[1]['datetime'] - timedelta(hours=1)], up_down='D').values('up_down').count() > 1:
                                flow_element.up_flow_trade = "B#1"
                                last_up_flow_time = ""

                    elif up_flow_list[-2:] == ['DN', 'DN']:
                        flow_element.up_flow_trade = "B#3"

                    if len(up_flow_element_list) > 1:
                        up_flow_element_list.pop(0)
                    up_flow_element_list.append(flow_element)

                    if len(up_flow_element_list) > 1:
                        if up_flow_element_list[0].up_flow_confirm is None and flow_element.up_flow_confirm == "UP":
                            flow_element.down_flow_trade = "S#2"
                            
                            
        if flow_element:
            flow_element.save()

        element = MinuteData()
        element.datetime = datetime
        element.open_price = open_price
        element.min_price = low_price
        element.max_price = high_price
        element.close_price = close_price
        element.avg_price = avg_price
        element.volume = volume
        element.flow = flow
        element.volume_rate = volume_rate
        element.volume_up_dn = volume_up_dn
        element.up_down = UD
        element.continue_up_down = continue_up_down
        element.hour_up_down = hour_up_down
        element.signal = signal
        element.signal_price = signal_price
        element.work_two_1_0 = now_work_1_0_1
        element.work_two_1_5 = now_work_1_5_1
        element.work_one_1_0 = now_work_1_0_2
        element.work_one_1_5 = now_work_1_5_2
        element.save()
        
        prev_up_down = UD
        
        
    start += 1000

2015-09-26 03:50:00
['U', 'U', 'U', 'U', 'S', 'S']
[236.11, 236.08, 236.01, 236, 235.85] [236.08, 236.01, 236, 236]
2015-09-26 06:55:00
['U', 'D', 'U', 'U', 'D', 'S']
[234.94, 234.9, 234.94, 234.83] [234.94, 234.88, 234.83]
2015-09-26 21:35:00
['U', 'U', 'D', 'U', 'S', 'U']
[234.87, 234.8, 234.34, 234.4] [234.87, 234.47, 234.4]
2015-09-28 12:10:00
['U', 'D', 'S', 'U', 'U', 'S']
[234.96, 234.91, 234.58, 234.58, 234.11] [234.6, 234.58, 234.06]
2015-09-28 12:50:00
['U', 'U', 'U', 'U', 'U', 'U']
[237.86, 238.23, 236.9, 236.5, 235.99, 234.9] [237.64, 237.53, 236.62, 236.05, 235.65, 234.85]
2015-09-28 16:30:00
['U', 'U', 'S', 'S', 'U', 'S']
[238.7, 238.2, 237.3, 237.3, 237.3] [238.39, 237.53, 237.3]
2015-09-28 17:30:00
['U', 'U', 'S', 'S', 'D', 'U']
[239.55, 239.3, 238.8, 238.8, 240.49, 239] [239.21, 239.28, 239]
2015-09-29 08:50:00
['U', 'D', 'U', 'D', 'D', 'U']
[240.59, 240.49, 240.57, 240.3, 240.5, 240.63] [240.37, 240.21, 240.08]
2015-09-29 09:45:00
['U', 'D', 'U', 'U', 'D', 'U']
[241.5,

2015-10-17 18:00:00
['U', 'U', 'U', 'U', 'U', 'S']
[270.74, 269.94, 269.83, 269.46, 268.48, 268.37] [270.14, 269.79, 269.56, 268.53, 268.2]
2015-10-17 18:20:00
['U', 'U', 'U', 'D', 'U', 'U']
[271.37, 271.21, 271.04] [271.19, 271.06, 270.99]
2015-10-17 19:35:00
['U', 'U', 'D', 'U', 'U', 'U']
[271.1, 270.83, 270.5, 270.57] [270.9, 270.83, 269.95]
2015-10-17 20:10:00
['U', 'U', 'U', 'D', 'S', 'D']
[271.26, 271.16, 270.74] [270.99, 271.16, 270.43]
2015-10-17 20:30:00
['U', 'U', 'S', 'D', 'U', 'U']
[271.81, 271.2, 271.05, 271.05, 271.26] [271.59, 271.2, 270.99]
2015-10-17 20:40:00
['U', 'D', 'U', 'U', 'S', 'D']
[272.09, 271.59, 271.81, 271.2] [271.56, 271.59, 271.2]
2015-10-17 21:40:00
['U', 'U', 'U', 'S', 'S', 'D']
[271.6, 270.58, 270.35, 270.2] [271.3, 270.58, 270.35]
2015-10-17 23:00:00
['U', 'D', 'U', 'U', 'U', 'S']
[275, 273.93, 273.56, 271.42] [273.51, 271.46, 270.9]
2015-10-17 23:10:00
['U', 'D', 'U', 'D', 'U', 'U']
[274.6, 274.5, 275, 273.93, 273.56] [274.11, 273.51, 271.46]
2015-10

2015-10-22 17:25:00
['U', 'U', 'U', 'S', 'S', 'S']
[272.19, 271.17, 270.62, 270.42] [271.52, 270.91, 270.62]
2015-10-22 17:35:00
['U', 'D', 'U', 'U', 'U', 'S']
[272.43, 272.15, 272.19, 271.17] [272.18, 271.52, 270.91]
2015-10-22 19:00:00
['U', 'U', 'S', 'U', 'D', 'S']
[274.99, 273.47, 272.45, 272.45] [273.55, 272.92, 272.27]
2015-10-22 19:15:00
['U', 'S', 'D', 'U', 'U', 'S']
[276.01, 274.74, 275.8, 274.99, 273.47] [274.91, 273.55, 272.92]
2015-10-22 19:25:00
['U', 'D', 'U', 'S', 'D', 'U']
[276, 275.15, 276.01, 274.74, 275.8, 274.99] [274.23, 274.91, 273.55]
2015-10-22 20:25:00
['U', 'U', 'U', 'U', 'S', 'U']
[279.8, 277.4, 276.56, 276.02, 275.63] [277.08, 275.98, 275.7, 275.41]
2015-10-22 23:05:00
['U', 'S', 'U', 'S', 'U', 'D']
[277.61, 276.89, 276.89, 276.36, 276.36] [277.12, 276.34, 276.22]
2015-10-22 23:35:00
['U', 'S', 'U', 'U', 'D', 'D']
[276.66, 276.5, 276.69, 276.34] [276.66, 276.5, 276.34]
2015-10-23 02:05:00
['U', 'U', 'S', 'S', 'U', 'S']
[275.9, 275.8, 275.5, 275.61, 275.52] [

2015-10-26 11:45:00
['U', 'U', 'U', 'U', 'U', 'D']
[287, 286.89, 286.98, 286.21, 285.52] [287, 285.51, 285.78, 285.49, 285.42]
2015-10-26 12:00:00
['U', 'S', 'D', 'U', 'U', 'U']
[287.41, 286.94, 287.68, 287, 286.89] [287.07, 287, 285.51]
2015-10-26 13:00:00
['U', 'D', 'S', 'D', 'U', 'U']
[287.83, 287.68, 288, 288.14, 288.08, 287.73] [287.6, 288.08, 287.4]
2015-10-26 14:15:00
['U', 'U', 'U', 'D', 'U', 'U']
[283.77, 283.38, 283.31] [283.36, 282.71, 282.63]
2015-10-26 14:25:00
['U', 'D', 'U', 'U', 'U', 'D']
[284.04, 285, 283.77, 283.38] [283.97, 283.36, 282.71]
2015-10-26 19:10:00
['U', 'D', 'U', 'U', 'S', 'D']
[284.21, 284.49, 284.87, 284.25] [283.96, 284.49, 283.72]
2015-10-26 20:30:00
['U', 'U', 'U', 'U', 'D', 'S']
[285.21, 284.61, 284.44, 283.82] [284.77, 284.61, 284.25, 283.45]
2015-10-26 20:50:00
['U', 'S', 'S', 'D', 'U', 'U']
[285.25, 284.73, 284.73, 285.51, 285.21, 284.61] [285.25, 284.77, 284.61]
2015-10-26 23:20:00
['U', 'D', 'S', 'U', 'S', 'U']
[288.13, 287.75, 288.13, 288.13, 

2015-10-29 07:00:00
['U', 'U', 'S', 'U', 'D', 'D']
[305.1, 304.99, 303.3, 303.3] [305.1, 304.5, 303.3]
2015-10-29 07:25:00
['U', 'S', 'U', 'U', 'D', 'U']
[306, 305.92, 305.92, 304.99] [305.93, 304.5, 303.2]
2015-10-29 07:40:00
['U', 'U', 'D', 'U', 'S', 'U']
[306.5, 306, 305.99, 306] [306.49, 306, 305.93]
2015-10-29 08:05:00
['U', 'D', 'U', 'U', 'D', 'U']
[306.68, 306.06, 306.69, 306.23] [306.36, 306.25, 305.62]
2015-10-29 08:15:00
['U', 'D', 'U', 'D', 'U', 'U']
[306.58, 306.58, 306.68, 306.06, 306.69] [306.58, 306.36, 306.25]
2015-10-29 08:45:00
['U', 'U', 'U', 'S', 'D', 'D']
[306.99, 306.95, 306.68, 305.97] [306.79, 306.72, 306.68]
2015-10-29 08:55:00
['U', 'D', 'U', 'U', 'U', 'S']
[307.23, 307.24, 306.99, 306.95] [306.75, 306.79, 306.72]
2015-10-29 09:55:00
['U', 'U', 'U', 'U', 'U', 'U']
[306.15, 305.97, 305, 304.39, 304.49, 304.3] [305.57, 305.2, 304.96, 304.39, 303.82, 303.34]
2015-10-29 10:05:00
['U', 'D', 'U', 'U', 'U', 'U']
[306.01, 306.08, 306.15, 305.97] [305.84, 305.57, 305.2

...

2021-08-13 09:10:00
['U', 'U', 'D', 'D', 'U', 'D']
[44670, 44540, 44425, 44431.5, 44450] [44514.5, 44387.5, 44380.5]
2021-08-13 10:05:00
['U', 'D', 'D', 'D', 'U', 'U']
[44615, 44546.5, 44584.5, 44620.5, 44647.5, 44572] [44487.5, 44559.5, 44395]
2021-08-13 10:25:00
['U', 'U', 'U', 'D', 'U', 'D']
[44800, 44748.5, 44522] [44711.5, 44522, 44453.5]
2021-08-13 10:45:00
['U', 'U', 'U', 'D', 'U', 'U']
[44914.5, 44917.5, 44805] [44786, 44764, 44707.5]
2021-08-13 11:15:00
['U', 'D', 'U', 'U', 'D', 'D']
[44883.5, 44901, 44905.5, 44819.5] [44861, 44824, 44748]
2021-08-13 11:55:00
['U', 'U', 'U', 'U', 'U', 'U']
[45340, 45194.5, 45053, 45041.5, 45079, 44966.5] [45194, 45053, 45028, 45020, 44937, 44892.5]
2021-08-13 13:45:00
['U', 'U', 'U', 'U', 'D', 'U']
[45299, 45199.5, 45200, 45030.5] [45199, 45175.5, 45030.5, 45000.5]
2021-08-13 14:45:00
['U', 'U', 'U', 'D', 'U', 'U']
[45381.5, 45348, 45280] [45348, 45279.5, 45241.5]
2021-08-13 15:45:00
['U', 'U', 'U', 'D', 'U', 'U']
[45936, 45777, 45752] [45750,

2021-08-15 04:45:00
['U', 'U', 'U', 'D', 'D', 'U']
[47362.5, 46852.5, 46803.5] [46852, 46804.5, 46685]
2021-08-15 05:45:00
['U', 'U', 'U', 'D', 'U', 'D']
[46618.5, 46593, 46527.5] [46565, 46500, 46407]
2021-08-15 06:25:00
['U', 'U', 'U', 'U', 'U', 'U']
[46785.5, 46765, 46760.5, 46706, 46700, 46657] [46765.5, 46656, 46706, 46655, 46626, 46588]
2021-08-15 07:00:00
['U', 'U', 'U', 'D', 'U', 'U']
[47028.5, 47091.5, 46968.5] [47010.5, 46945, 46930]
2021-08-15 07:30:00
['U', 'D', 'U', 'U', 'D', 'D']
[47105, 47248.5, 47240, 47027] [47055, 47027.5, 46931]
2021-08-15 08:35:00
['U', 'U', 'U', 'U', 'U', 'U']
[47164, 47167.5, 47201.5, 47095, 46968.5, 46970.5] [47083.5, 47095.5, 47090.5, 46960, 46926.5, 46870]
2021-08-15 09:10:00
['U', 'U', 'U', 'D', 'D', 'U']
[47185, 47197.5, 47100] [47145, 47100, 47063]
2021-08-15 10:00:00
['U', 'U', 'U', 'D', 'U', 'D']
[47220, 47149, 47091] [47140, 47069, 47004]
2021-08-15 10:10:00
['U', 'D', 'U', 'U', 'U', 'D']
[47214.5, 47238, 47220, 47149] [47143.5, 47140, 47

2021-08-17 12:35:00
['U', 'U', 'U', 'U', 'U', 'U']
[46546.5, 46521.5, 46476.5, 46440, 46383.5, 46383.5] [46460.5, 46444.5, 46371, 46380, 46377, 46334]
2021-08-17 13:15:00
['U', 'D', 'U', 'D', 'U', 'D']
[46583, 46506.5, 46507, 46439.5, 46433] [46498.5, 46387.5, 46368.5]
2021-08-17 13:40:00
['U', 'U', 'U', 'D', 'D', 'U']
[46407.5, 46350.5, 46350.5] [46320.5, 46273.5, 46270]
2021-08-17 13:55:00
['U', 'U', 'D', 'U', 'U', 'U']
[46460, 46448, 46408, 46407.5] [46406.5, 46368, 46320.5]
2021-08-17 14:30:00
['U', 'U', 'U', 'D', 'U', 'D']
[46462.5, 46368, 46184] [46368, 46184, 46026]
2021-08-17 15:30:00
['U', 'D', 'U', 'U', 'D', 'D']
[46050.5, 46015, 46011, 45947.5] [45921.5, 45872, 45819.5]
2021-08-17 17:10:00
['U', 'U', 'U', 'U', 'D', 'U']
[46136, 46027, 45949.5, 45919] [45999, 45874.5, 45888.5, 45859]
2021-08-17 17:30:00
['U', 'U', 'U', 'D', 'U', 'U']
[46320, 46167.5, 46099.5] [46111.5, 46068, 45977]
2021-08-17 17:45:00
['U', 'D', 'D', 'U', 'U', 'U']
[46289, 46270, 46348.5, 46320, 46167.5] [46

2021-08-19 17:05:00
['U', 'U', 'U', 'D', 'U', 'U']
[44973, 44650, 44339.5] [44651, 44322.5, 44216.5]
2021-08-19 17:35:00
['U', 'U', 'U', 'D', 'D', 'D']
[44818.5, 44755, 44550] [44658.5, 44491, 44385]
2021-08-19 18:05:00
['U', 'U', 'U', 'D', 'D', 'D']
[44799.5, 44777.5, 44670.5] [44685, 44611, 44586]
2021-08-19 18:15:00
['U', 'D', 'U', 'U', 'U', 'D']
[44795, 44839, 44799.5, 44777.5] [44692, 44685, 44611]
2021-08-19 18:45:00
['U', 'D', 'U', 'U', 'D', 'D']
[44830, 44833.5, 44829, 44766] [44720.5, 44720, 44625.5]
2021-08-19 20:35:00
['U', 'D', 'D', 'U', 'U', 'D']
[44462.5, 44418, 44480, 44448, 44380] [44342.5, 44290.5, 44217.5]
2021-08-19 21:30:00
['U', 'U', 'U', 'U', 'D', 'D']
[44455, 44417, 44325, 44270] [44350.5, 44290.5, 44231, 44149.5]
2021-08-19 22:15:00
['U', 'U', 'U', 'U', 'D', 'D']
[44695, 44669, 44587.5, 44606.5] [44597.5, 44580.5, 44501, 44418.5]
2021-08-19 23:20:00
['U', 'U', 'U', 'U', 'U', 'U']
[45445.5, 45269.5, 45345, 45155, 44965, 44965] [45242, 45138.5, 45123.5, 44965, 448

TypeError: string indices must be integers